# Stock Price Prediction for the 5 Biggest Brazilian Commodity-Base Companies  

<img src='./Images/image_1.jpg' style="width:90%; height:500px">


## 1. Overview
### 1.1. Motivation
The stock price market might seems chaotic at a first glance. There is a lot of information that must be taken into account in order to decide whether to buy or not a stock. Some say that the Fundamental Analysis\[1] is the right way to decide whether or not to buy a stock, and some say that the Technical Analysis\[2].

Based on this lack of convergence about which method should be used, and once that we can find a giant amount of data, a data science project could be a nice fit to predict the behaviour of the prices in the next day. Therefore we could use these predictions to guide the decisions.

Nowadays, besides corona crises, the markets of the USA are on their historic maximum. This fact means that there is not so much place to find a share of business with good profits possibilities. Therefore, when we would like to have a bigger profit, we must take more risk and investments that fit this profile are those in emergent markets, like Brazil, India, China, etc. I’m a chemical engineer from Brazil and to use data science to understand the market behaviour for the next weeks are a topic that interests me a lot and can bring my education, my experience living here and my data science skills together.

As we know, the commodity is an economic good that is often used as input the production of other goods or services. These goods have full or substantial fungibility, that is, they can be treated as equivalent (or nearly) regardless of who produced them. Some examples are coffee, gold ore, iron ore, oil, water, electric power, etc. Brazil is a land that has a commodity-based economy\[3] and to be able to predict the share prices of business that work in some level with commodities, cold be an excellent opportunity for discovering bad and good calls.

Besides that, nowadays there are lots of discussions about a commodity rally in 2021\[4]\[5]\[6]\[7]. That means, understanding the future of these goods and being able the share price of the companies or even the commodity itself like gold or silver, are key points to have success investing in Brazil.

So let’s dive in the Brazilian Stock Prices of commodity-based companies, explore them and predict its prices! 


### 1.2. Problem Statement
As mention above, our interest lay on the future share price of commodity-based companies. It gets even more dramatic with 2021 bringing the potential for a commodity rally. To predict those stock prices are a big prize.
**Based on this, we can define that our problem is to analyse the 5 biggest commodity-based companies in Brazil in order to understand their behaviour and relationships as well to get a deeper understanding about what we are going to predict. Then, an algorithm as well its pipeline will be designed and implemented in order to predict the prices for the future.** 


### 1.3. Data and Inputs  
The data will be gathered using the Yahoo! Finance API. A great tutorial (unfortunately only in Portuguese) can be found in this [medium post](https://medium.com/@rodrigobercinimartins/como-extrair-dados-da-bovespa-sem-gastar-nada-com-python-14a03454a720). The library yahooquery gives us all tools to colect the data as we want.  

We will gather data of the 5 biggest commodity-based companies in Brazil, that are:
- Petrobras (PETR4): largest Brazilian company, Petrobras produces oil;
- Vale (VALE3): the company is among the largest companies in Brazil, and is the largest producer of iron ore in the world;
- CSN (CSNA3): it is the largest steel industry in Brazil and Latin America, and one of the largest in the world;
- JBS (JBSS3): the company is one of the largest producers of animal protein in the world;
- Suzano (SUZB3): the company is considered the largest producer of eucalyptus pulp of the world;

The data will be divided into 7 features for each day: lowest, highest, open, closed and adjusted close price, as well as volume and ticker.

### 1.4. General Outline   
       a. Gathering the Data;
       b. Cleaning and Exploration;
              b.1. Checking missing values and a first look at the data;
              b.2. Checking the variation of the data over time with a line graph;
              b.3. Using the Moving Average to get another view of price variation;
              b.4. Visualization of Volumes over time;
              b.5. Daily Return;
              b.6. Risk Analysis;
       c. Model Building;
       d. Making Predictions;
       e. Conclusion and Next Steps;      
    




In [1]:
# loading packages and utilities
import numpy as np
import pandas as pd
import tensorflow as tf
import datetime
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px

from plotly.subplots import make_subplots
from tensorflow import keras
from yahooquery import Ticker
from sklearn.preprocessing import MinMaxScaler

%matplotlib inline

In [2]:
def gather_stocks(company_name_list, start = '2007-01-01', end = datetime.date.today()):
    """get the name of the companies, as well as the start and end date, check if they are with the
    ".SA" ending and create a dataframe.
    """
    def name_check(name):
        if name[-2:] != "SA":
            name = name + ".SA"
        return name
    company_name_list = list(map(name_check, company_name_list))

    df = pd.DataFrame(Ticker(company_name_list).history(start = start, end = end)).reset_index()
    return df


### a. Loading the data through Yahoo API

In order to have something to compare, let's gather also data of two ETFs indexes. By having these two indexes we can say if our portfolio is performing better than a basic index. In other words, we will have a winning condition!
The indexes are:
- IBVV11 that replicates IBOVESPA, the benchmark of the 70 biggest Brazilian companies;
- SPXI11 that replicates S&P500.  

Both are managed by Itau Bank, the biggest bank of south America and can be gathered using the Yahooquery API!

In [3]:
# listing the companies and gathering the data
stock_list = ["PETR4.SA", "VALE3.SA", "CSNA3.SA", "JBSS3.SA", "SUZB3.SA", "BOVV11.SA", "SPXI11.SA"]
start_date = '2007-01-01' #one year before the comodities rally in Brasil
end_date = datetime.date.today() #today
df = gather_stocks(stock_list, start = start_date, end = end_date)

In [4]:
df.head()

symbol        date   close       high      volume        low   open  \
0  PETR4.SA  2007-01-02  25.160  25.225000  10244800.0  24.879999  25.00   
1  PETR4.SA  2007-01-03  24.395  25.200001  19898600.0  24.004999  25.08   
2  PETR4.SA  2007-01-04  23.850  24.375000  21060200.0  23.700001  24.25   
3  PETR4.SA  2007-01-05  23.125  23.995001  24864000.0  22.549999  23.60   
4  PETR4.SA  2007-01-08  23.395  23.570000  19440200.0  22.900000  23.25   

    adjclose  dividends  splits  
0  18.318081      0.225     0.0  
1  17.761106      0.000     0.0  
2  17.364315      0.000     0.0  
3  16.836473      0.000     0.0  
4  17.033047      0.000     0.0

### b. Cleaning and EDA
Now that we gathered some data, let's start the exploration.

### b.1. Checking missing values and a first look at the data

In [5]:
# checkig for missing values
df.isnull().sum()

symbol       0
date         0
close        0
high         0
volume       0
low          0
open         0
adjclose     0
dividends    0
splits       0
dtype: int64

In [6]:
# checking the infos of the dataset
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19899 entries, 0 to 19898
Data columns (total 10 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   symbol     19899 non-null  object 
 1   date       19899 non-null  object 
 2   close      19899 non-null  float64
 3   high       19899 non-null  float64
 4   volume     19899 non-null  float64
 5   low        19899 non-null  float64
 6   open       19899 non-null  float64
 7   adjclose   19899 non-null  float64
 8   dividends  19899 non-null  float64
 9   splits     19899 non-null  float64
dtypes: float64(8), object(2)
memory usage: 1.5+ MB


In [7]:
df.date.unique().shape

(3498,)

In [8]:
df.symbol.unique()

array(['PETR4.SA', 'VALE3.SA', 'CSNA3.SA', 'JBSS3.SA', 'SUZB3.SA',
       'BOVV11.SA', 'SPXI11.SA'], dtype=object)

There are 3496 instances for each company. As we will work with 5 companies and 2 indexes, there are in total 24479 instances for each of the 7 columns and no missing values.

In [9]:
# Checking the earliest instance for each Stock
for stock in stock_list:
    print(df[df.symbol == stock].date.min(), stock)

2007-01-02 PETR4.SA
2007-01-02 VALE3.SA
2007-01-02 CSNA3.SA
2007-03-29 JBSS3.SA
2007-05-10 SUZB3.SA
2016-07-29 BOVV11.SA
2015-01-30 SPXI11.SA


We can notice that all the 5 stocks that we are interested in, are from 2005 and the latest one is SUZB3 from 2007-05-10. So we have data to start, so our model will start on the same page.  

Another important point is that BOVV11 starts on 2016-07-29 and 2015-01-30. Though the registration starts years later it is not a problem at all, once we will use these two indexes just for comparing with our portfolio of commodity-base companies.

Now let's check some statistcs for the stocks.

In [10]:
for stock in stock_list:
    print(df[df.symbol == stock].describe(), stock, "\n\n\n")

             close         high        volume          low         open  \
count  3498.000000  3498.000000  3.498000e+03  3498.000000  3498.000000   
mean     22.195515    22.550629  3.976148e+07    21.866830    22.223664   
std       8.429643     8.530013  3.087688e+07     8.327597     8.439627   
min       4.200000     4.270000  0.000000e+00     4.120000     4.200000   
25%      16.122500    16.389999  2.042900e+07    15.900000    16.150000   
50%      21.680000    22.059999  3.137120e+07    21.405000    21.745000   
75%      27.290001    27.617501  5.194938e+07    26.940001    27.299999   
max      52.509998    53.680000  6.989506e+08    51.950001    52.580002   

          adjclose    dividends  splits  
count  3498.000000  3498.000000  3498.0  
mean     18.950569     0.002204     0.0  
std       6.402566     0.028307     0.0  
min       3.896351     0.000000     0.0  
25%      14.678572     0.000000     0.0  
50%      18.419478     0.000000     0.0  
75%      23.454119     0.00000

Here there are a couple of things that must be noticed. They are:
- Std of the volume is pretty high, meaning that there is pretty much variance. It is valid for all stocks;
- Min and Max price of AdjClose are also big. It means that their values increased tremendously;
- Looking at the split column, we can see that only SUZB3 was split along with the timespan we are working with;
- VALE3 paid the highest dividend in order of 2.407510
- With a mean of 0.002434 we can say CSNA3 pays more dividends on average that the other 4 companies.  


Now let's plot some line graphs to observe the variation of the prices over time!

### b.2. Checking the variation of the data over time with a line graph

In [77]:
fig = px.line(df, x = "date", y = "adjclose",
              color = 'symbol',
              title = "Stock Prices over Time",
              width = 1100, height = 600)
fig.show()

This comparison in terms of absolute price is the first step, but it will be easier to compare when we work with scaled values. 
  
For the Forecasting step, we need to scale each stock separately. But for purpose of variance comparison, we can scale all data together.

In [12]:
df.adjclose.values

array([ 18.3180809 ,  17.76110649,  17.36431503, ..., 223.22999573,
       224.53999329, 222.66999817])

In [78]:
scaler = MinMaxScaler()
df_adjclose_scaled = df.copy()
df_adjclose_scaled.adjclose = scaler.fit_transform(df.adjclose.values.reshape(-1, 1))

In [79]:
fig = px.line(df_adjclose_scaled, x = "date", 
              y = "adjclose", color = 'symbol', 
              title = "Scaled Stock Prices over Time",
              width = 1100, height = 600)
fig.show()

Looking at both graphs we can infer the following:
- Among the 5 stocks, VALE3 reached the highest price both in 2008 and also now in 2020/2021;  

- A big difference is SUZB3. From 2008 until 2018 the company shows a constant price. It means we can't compare the data before 2018 and it may indicate a failure of registration or even that the company wasn't in the stock market until then;  

- After 2018 SUZB3 shows a strong increase in its value, something from around 19.81 to 74.04, increasing 373.75% in 3 years;  

- For the other 3 Stocks, we can see that they walk around but did not increase their value at all along all these years;   

- Another point to see is these 3 Stocks have today similar prices like 2008 when there was a commodity rally. Though 2020 was atypical because of the corona, we can notice a strong increase in their prices. When we compare 2008 and 2020/2021 we can see similar behaviours;  

- Both indexes increase their values over time but we can clearly notice that S&P500 recovered the prices pre corona and skyrocket to a record level and BOVESPA is still walking around very slowly. **It means, we might be seeing an opportunity in the Brazilian market.**

### b.3. Using the Moving Average to get another view of price variation 

In order to visualize a less noisy behaviour and variations let's use now **moving average.** To do so, we need first generate the moving avg for each stock data and then plot it.

In [76]:
fig = make_subplots(rows = 7, cols = 1,
                    subplot_titles = [f"Comparing {i} with its on moving avg of 10 days." for i in stock_list])

for i in range(1,8):
    
    fig.add_trace(
        go.Scatter(x = df[df.symbol == stock_list[i - 1]].date, 
                   y = df[df.symbol == stock_list[i - 1]].adjclose,
                    mode = 'lines',
                    name = stock_list[i - 1]),
                    row = i, col = 1)

    fig.add_trace(
        go.Scatter(x = df[df.symbol == stock_list[i - 1]].date, 
                   y = df[df.symbol == stock_list[i - 1]].adjclose.rolling(10).mean(),
                    mode = 'lines',
                    name = stock_list[i - 1] + " MM"),
                    row = i, col = 1)

fig.update_layout(width = 1100, height = 3000)
fig.show()

Now we can see the price variation for each stock with less noise. Indeed, without a zoom, it seems that nothing change at all, but plotly give us the possibility of zoom in and when we do it, we notice a much smoother line.  
It is especially good when we are observing a peak between 2008 and 2020/2021.  
   
If you have some knowledge of technical analysis, the MA will also be helpful to identify trends and behaviours. Unfortunately, I don't possess, by now, this set of skills, but luckily we can bypass this lack using the ML models.

### b.4. Visualization of Volumes over time

We must understand the trading volume, the flow, as the market fuel. A large flow, a large volume of trading means that a certain directional movement - bullish, for example - is sustained.

In [36]:
fig = px.line(df, x = "date", y = "volume",
              color = 'symbol',
              title = "Stock Volumes over Time",
              width = 1100, height = 600)
fig.show()

Looking stock by stock, separately, we may conclude the following:
- In descending order of volume we have PETR4, VALE3, CSNA3, JBSS3 and SUZB3;
- As expected, the ETFs have the lowest volumes;
- Though the price is increasing, the volumes are also increasing. It might mean that the investors believe that the companies still at interesting prices;
- Independent of the share and the date that it started, there is an increase in volume. We can also notice that this behaviour got stronger and for 2020 and 2021 there is a visible growth of the volumes. **It may show that there is really a bullish tendency.**


### b.5. Daily Return

Though investing for the long term is usually recommended, it can be fun to measure your daily gains — or not so much fun to measure your daily losses — especially after a particularly good or bad day for the market. So we can define a winning condition (some % of gain) or a stop loss (also in %).



In [34]:
# Creating the Daily Return feature
return_list = []
for stock in stock_list:
    return_list.extend(df[df.symbol == stock].adjclose.pct_change())

df['daily_return'] = np.array(return_list)

In [35]:
fig = px.line(df, x = "date", y = "daily_return",
              color = 'symbol',
              title = "Daily Return over Time",
              width = 1100, height = 600)
fig.show()

Here we can observe the following:
- For PETR4 the most part of the fluctuation was within the range of +- 10%;
- All the stocks present a strong negative variation in something in March or April. This is the effect of Covid-19; 
- After this time with huge fluctuation, the behaviour got normal (the range that they had before). It shows that though pandemic is a very noise time for investing, the prices didn't experience strong variation after the first days of the crisis; 
- This maintenance of behaviour brings confidence for the long term investor as well as for the day-trading because there is some visibility in the price variation.

### b.6. Risk Analysis   

Now we finally can to state which companies are riskier by using the mean and standard deviation of the daily variation.

In [74]:
daily_return_mean = []
daily_return_std = []
for stock in stock_list:
    daily_return_mean.append(df[df.symbol == stock].daily_return.mean())
    daily_return_std.append(df[df.symbol == stock].daily_return.std())

In [75]:
fig = go.Figure()
fig.add_trace(go.Scatter(x = daily_return_mean,
                  y = daily_return_std,
                  mode = "markers+text",
                  marker = dict(size = 10),
                  text = stock_list,
                  textposition='top center'))


fig.update_layout(width = 1100, height=500,
                  title_text='Risk and Expected return for each company')
fig.update_xaxes(title_text = "Expected Return")
fig.update_yaxes(title_text = "Risk")

fig.show()

Using this graph, we can select and establish some order in which companies bring more return with less risk within. That means we want companies that lay far in the x-axes and have lower values for y-axes. So as we notice, this visualization is very helpful for making decisions. 
Through the graph we can state the following:
- The two index ETFs have low-risk associate and SPXI11 has the most desired profile: lowest risk and the second-highest expected return;
- PETR4 doesn't seem a good choice at all. High Risk and lowest expected return isn't a good fit for the portfolio;
- VALE3 was the highest-priced stock in the 2008 rally, it is also the highest 2021, we find it with an interesting position with intermediate values both for expected return and for risk;
- SUZB3 the second-highest priced stock has both the low expected return and low risk. So it could be a safe paper to have in the portfolio;
- CSNA3 has also both, the highest expected return and the highest risk. It is still interesting to have in the portfolio, once we want to balance SUZB3.
- Of these 5 companies we should consider, in a real live portfolio, if we want to keep PETR4 and JBSS3. But as we want to create a portfolio for a possible commodity rally, JBSS3 can be easily considered. The only PETR4 due to its low expected return and high risk haven't an interesting profile for the future.


Here we finish the exploration part and let's move forward to modelling part!